In [1]:
using Dates, MortalityTables, DifferentialEquations,Plots, ColorSchemes, DayCounts

┌ Info: Precompiling DifferentialEquations [0c46a032-eb83-5123-abaf-570d42b7fbaa]
└ @ Base loading.jl:1273
┌ Info: Precompiling Plots [91a5bcdd-55d7-5caf-9e0b-520d859cae80]
└ @ Base loading.jl:1273
┌ Info: Precompiling ColorSchemes [35d6a980-a343-548e-a6ea-1d62b119f2f4]
└ @ Base loading.jl:1273
┌ Info: Precompiling DayCounts [44e31299-2c53-5a9b-9141-82aa45d7972f]
└ @ Base loading.jl:1273


In [3]:
const mt = MortalityTables
tables = mt.tables()
cso = tables["2001 CSO Super Preferred Select and Ultimate - Male Nonsmoker, ANB"]

MortalityTable:
   Name:
       2001 CSO Super Preferred Select and Ultimate - Male Nonsmoker, ANB
   Provider:
       American Academy of Actuaries
   mort.SOA.org ID:
       1076
   mort.SOA.org link:
       https://mort.soa.org/ViewTable.aspx?&TableIdentity=1076
   Description:
       2001 Commissioners Standard Ordinary (CSO) Super Preferred Select and Ultimate Table – Male Nonsmoker. Basis: Age Nearest Birthday. Minimum Select Age: 0. Maximum Select Age: 99. Minimum Ultimate Age: 16. Maximum Ultimate Age: 120


In [4]:
function duration(d1,d2)
    y1,m1,d1 = Dates.yearmonthday(d1)
    y2,m2,d2 = Dates.yearmonthday(d2)

    return max(y2 - y1 - ((m2, d2) < (m1,d1)) + 1,0)
end

duration (generic function with 1 method)

Here, policy mechanics are coded. It's essentially a discrete differential equation, so it leverages `DifferentialEquations.jl`

In [4]:
function policy_projection(dvars,vars,p,t)
    
    # static parameters
    int_rate = p[:int_rate]
    issue_date = p[:issue_date]
    issue_age = p[:issue_age]
    face = p[:face]
    ann_prem = p[:annual_prem]
    
    # the projection variables
    av = vars[1]
    
    # calculated variables
    cur_date = issue_date + Day(t)
    dur = duration(issue_date,cur_date)
    att_age = issue_age + dur - 1
    lapsed = (av <= 0.0 ) & (t > 0)

    
    if !lapsed 


        monthly_coi_rate = (1 - (1-qx(p[:mort_assump],issue_age,dur)) ^ (1/12))




        # initial checks
        if Dates.day(issue_date) >= 28
            error("Issue date will cause problems for shorter months.")
        end

        # annual events
        if Dates.monthday(cur_date) == Dates.monthday(issue_date)
            premium = ann_prem
            bonus = 0.0
            dvars[3] += 1.0
        else
            premium = 0.0
            bonus = 0.0
            dvars[3] += dvars[3]
        end

        # monthly_events
        if Dates.day(cur_date) == Dates.day(issue_date)
            coi = max((face - av) * monthly_coi_rate,0.0)
        else
            coi = 0.0
        end

        # daily events
        int(av) = av * ((1 + int_rate) ^ (1 / 360) - 1.0)


        # dynamic events

        # track vars

        dvars[2] = premium
        dvars[3] = dur
        
        # av
        dvars[1] = max(0.0,av + premium + int(av) + bonus - coi) 
        
    else
        dvars[1] = 0.0
        dvars[2] = 0.0
        dvars[3] = dur
    end
    
end



policy_projection (generic function with 1 method)

Define some of the parameters for the policy we want to project. These values are accessible within the projection.

In [5]:
# eventually convert this into a type but for interactivty using Dict for now
params(prem,int) = Dict(
    :int_rate => int,
    :issue_date => Date(2010,1,1),
    :face => 1e6,
    :issue_age => 25,
    :mort_assump => tables["2001 CSO Super Preferred Select and Ultimate - Male Nonsmoker, ANB"],
    :projection_years => 75,
    :annual_prem => prem
)

params (generic function with 1 method)

Running one projection with the given annual premium and interest crediting rate:

In [6]:
p = params(8000.0,0.08)

Dict{Symbol,Any} with 7 entries:
  :issue_date       => 2010-01-01
  :int_rate         => 0.08
  :annual_prem      => 8000.0
  :mort_assump      => MortalityTable(Union{Missing, Float64}[missing missing ……
  :face             => 1.0e6
  :projection_years => 75
  :issue_age        => 25

In [7]:
# calculate the number of days to project
projection_end_date = p[:issue_date] + Year(p[:projection_years]) 
days_to_project = Dates.value(projection_end_date - p[:issue_date])
        
# the [0.0,..] are the initial conditions for the tracked variables
prob = DiscreteProblem(policy_projection,[0.0,0.0,0],(0,days_to_project),p)
proj = solve(prob,FunctionMap())

retcode: Success
Interpolation: left-endpoint piecewise constant
t: 27395-element Array{Int64,1}:
     0
     1
     2
     3
     4
     5
     6
     7
     8
     9
    10
    11
    12
     ⋮
 27383
 27384
 27385
 27386
 27387
 27388
 27389
 27390
 27391
 27392
 27393
 27394
u: 27395-element Array{Array{Float64,1},1}:
 [0.0, 0.0, 0.0]       
 [7975.83, 8000.0, 1.0]
 [7977.54, 0.0, 1.0]   
 [7979.24, 0.0, 1.0]   
 [7980.95, 0.0, 1.0]   
 [7982.65, 0.0, 1.0]   
 [7984.36, 0.0, 1.0]   
 [7986.07, 0.0, 1.0]   
 [7987.77, 0.0, 1.0]   
 [7989.48, 0.0, 1.0]   
 [7991.19, 0.0, 1.0]   
 [7992.9, 0.0, 1.0]    
 [7994.61, 0.0, 1.0]   
 ⋮                     
 [3.50663e7, 0.0, 75.0]
 [3.50738e7, 0.0, 75.0]
 [3.50813e7, 0.0, 75.0]
 [3.50888e7, 0.0, 75.0]
 [3.50963e7, 0.0, 75.0]
 [3.51039e7, 0.0, 75.0]
 [3.51114e7, 0.0, 75.0]
 [3.51189e7, 0.0, 75.0]
 [3.51264e7, 0.0, 75.0]
 [3.51339e7, 0.0, 75.0]
 [3.51414e7, 0.0, 75.0]
 [3.51489e7, 0.0, 75.0]

Plot the account value, annual premium, and duration

In [8]:
plot(proj)

Project the account value at attained age 100 and the age at which the policy lapses for the given combination of premium and crediting rate

In [9]:
prem_range = 1000.0:100.0:9000.0
int_range = 0.02:0.0025:0.08

function ending_av(ann_prem,int,days_to_project)
    p = params(ann_prem,int)
    prob = DiscreteProblem(policy_projection,[0.0,0.0,0],(0,days_to_project),p)
    proj = solve(prob,FunctionMap())
    end_av = proj[end][1] 
    if end_av == 0.0
        lapse_time = findfirst(isequal(0.0),proj[1,2:end])
    else
        lapse_time = length(proj)
    end
    duration = proj[3,lapse_time]
    end_age = p[:issue_age] + duration - 1.0
    
    return end_av,end_age
    
end

end_age = zeros(length(prem_range),length(int_range))
end_av = zeros(length(prem_range),length(int_range))
@time begin
    for (i,vp) in enumerate(prem_range)
        for (j,vi) in enumerate(int_range)
            (end_av[i,j],end_age[i,j]) = ending_av(vp,vi,days_to_project)
        end
    end
end

 52.446618 seconds (951.67 M allocations: 22.033 GiB, 4.92% gc time)


In [10]:
contour(int_range,prem_range,[end_av,end_age], layout =2, size=(950, 600),contour_labels=true,c=:bkr,fill=true)

The number of policy projection days computed:

In [13]:
using ColorSchemes

In [15]:
contour(int_range,prem_range,[end_av,end_age], layout =2, size=(950, 600),contour_labels=true,c=cgrad(ColorSchemes.turbo.colors),fill=true)

In [11]:
length(end_av) *  days_to_project

55472850